In [1]:
from matplotlib import pyplot as plt
from matplotlib.image import imread
import pandas as pd
from collections import Counter
import json
import os
import re
import tempfile
import numpy as np
from os.path import exists
from imblearn.under_sampling import RandomUnderSampler
from PIL import ImageFile
import sklearn as sk
from sklearn.model_selection import train_test_split, StratifiedShuffleSplit
import tensorflow as tf
import tensorflow.keras
from tensorflow.keras.preprocessing.image import ImageDataGenerator
from tensorflow.keras.layers import Conv2D, MaxPooling2D, Dense, Dropout, Flatten, Activation
from tensorflow.keras.models import Sequential
from tensorflow.keras.optimizers import Adam
# custom modules
import image_faults

ImageFile.LOAD_TRUNCATED_IMAGES = True

In [2]:
def dict_pics_jup():
    '''
    {source:target} dict used to replace source urls with image location as input
    '''
    target_dir = os.getcwd() + os.sep + "training_images"
    with open('temp_pics_source_list.txt') as f:
        temp_pics_source_list = json.load(f)
        
    dict_pics = {}
    for k in temp_pics_source_list:
         patt_1 = re.search(r'[^/]+(?=/\$_|.(\.jpg|\.jpeg|\.png))', k, re.IGNORECASE)
         patt_2 = re.search(r'(\.jpg|\.jpeg|\.png)', k, re.IGNORECASE)
         if patt_1 and patt_2 is not None:
             tag = patt_1.group() + patt_2.group().lower()
             file_name = target_dir + os.sep + tag
             dict_pics.update({k:file_name})
    print("{source:target} dictionary created @ " + target_dir)
    return dict_pics

In [3]:
# image_faults.faulty_images() # removes faulty images
df = pd.read_csv('expanded_class.csv', index_col=[0], low_memory=False)

In [4]:
dict_pics = dict_pics_jup()

with open('women_cat_list.txt') as f:
    women_cats = json.load(f)
with open('men_cat_list.txt') as f:
    men_cats = json.load(f)
    
with open('temp_pics_source_list.txt') as f:
    tempics = json.load(f)
# list of image urls that did not get named properly which will be removed from the dataframe
drop_row_vals = []
for pic in tempics:
    try:
        dict_pics[pic]
    except KeyError:
        drop_row_vals.append(pic)

df['PrimaryCategoryID'] = df['PrimaryCategoryID'].astype(str) # pandas thinks ids are ints
ddf = df[df.PictureURL.isin(drop_row_vals)==False] # remove improperly named image files
df = ddf[ddf.PrimaryCategoryID.isin(men_cats)==False] # removes rows of womens categories

blah = pd.Series(df.PictureURL)
df = df.drop(labels=['PictureURL'], axis=1)

blah = blah.apply(lambda x: dict_pics[x])
df = pd.concat([blah, df],axis=1)
df = df.groupby('PrimaryCategoryID').filter(lambda x: len(x)>25) # removes cat outliers

{source:target} dictionary created @ /tf/training_images


In [5]:
df=df.sample(frac=1)

In [6]:
undersample = RandomUnderSampler(sampling_strategy='auto')
train, y_under = undersample.fit_resample(df, df['PrimaryCategoryID'])
#print(Counter(train['PrimaryCategoryID']))

In [7]:
train, test = train_test_split(train, test_size=0.2, random_state=42)
# stratify=train['PrimaryCategoryID']
# train['PrimaryCategoryID'].value_counts()

In [8]:
datagen = ImageDataGenerator(rescale=1./255., 
                             validation_split=.2,
                             #samplewise_std_normalization=True,
                             #horizontal_flip= True,
                             #vertical_flip= True,
                             #width_shift_range= 0.2,
                             #height_shift_range= 0.2,
                             #rotation_range= 90,
                             preprocessing_function=tf.keras.applications.inception_resnet_v2.preprocess_input)
train_generator=datagen.flow_from_dataframe(
    dataframe=train[:len(train)],
    directory='./training_images',
    x_col='PictureURL',
    y_col='PrimaryCategoryID',
    batch_size=32,
    seed=42,
    shuffle=True,
    target_size=(299,299),
    subset='training'
    )
validation_generator=datagen.flow_from_dataframe(
    dataframe=train[:len(train)], # is using train right?
    directory='./training_images',
    x_col='PictureURL',
    y_col='PrimaryCategoryID',
    batch_size=32,
    seed=42,
    shuffle=True,
    target_size=(299,299),
    subset='validation'
    )

Found 4444 validated image filenames belonging to 7 classes.
Found 1111 validated image filenames belonging to 7 classes.


In [9]:
imgs, labels = next(train_generator)

In [10]:
def plotImages(images_arr):
    fig, axes = plt.subplots(1, 10, figsize=(20,20))
    axes = axes.flatten()
    for img, ax in zip( images_arr, axes):
        ax.imshow(img)
        ax.axis('off')
    plt.tight_layout()
    plt.show()

In [11]:
#plotImages(imgs)
#print(labels)

In [12]:
physical_devices = tf.config.list_physical_devices('GPU')
print(len(physical_devices))
tf.config.experimental.set_memory_growth(physical_devices[0], True)

1


In [13]:
# see https://www.kaggle.com/dmitrypukhov/cnn-with-imagedatagenerator-flow-from-dataframe for train/test/val split 
# example

# may need to either create a test dataset from the original dataset or just download a new one

In [14]:
base_model = tf.keras.applications.inception_resnet_v2.InceptionResNetV2(include_top=False, weights='imagenet', pooling='avg')
#base_model.summary()

In [15]:
for layer in base_model.layers:
    layer.trainable = True
    
output = Dense(7, activation='softmax')(base_model.output)
model = tf.keras.Model(base_model.input, output)
#model = add_regularization(model)
model.summary()


Model: "model"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_1 (InputLayer)           [(None, None, None,  0           []                               
                                 3)]                                                              
                                                                                                  
 conv2d (Conv2D)                (None, None, None,   864         ['input_1[0][0]']                
                                32)                                                               
                                                                                                  
 batch_normalization (BatchNorm  (None, None, None,   96         ['conv2d[0][0]']                 
 alization)                     32)                                                           

In [16]:
#model.add(Dropout(.5))
#model.add(Dense(64, activation='softmax'))
# model.add(Dropout(.25))
#model = add_regularization(model)


In [17]:
model.compile(optimizer=Adam(learning_rate=.0001), loss='categorical_crossentropy',
              metrics=['accuracy'])
# sparse_categorical_crossentropy

In [ ]:
model.fit(x=train_generator,
          steps_per_epoch=len(train_generator),
          validation_data=validation_generator,
          validation_steps=len(validation_generator),
          epochs=30,
          verbose=1)

Epoch 1/30
139/139 [==============================] - 65s 390ms/step - loss: 1.0030 - accuracy: 0.6427 - val_loss: 2.1331 - val_accuracy: 0.1620
Epoch 2/30
139/139 [==============================] - 51s 365ms/step - loss: 0.3751 - accuracy: 0.8756 - val_loss: 1.7818 - val_accuracy: 0.4707
Epoch 3/30
139/139 [==============================] - 50s 359ms/step - loss: 0.1193 - accuracy: 0.9622 - val_loss: 1.5616 - val_accuracy: 0.6166
Epoch 4/30
139/139 [==============================] - 51s 363ms/step - loss: 0.0830 - accuracy: 0.9750 - val_loss: 1.3374 - val_accuracy: 0.6922
Epoch 5/30
139/139 [==============================] - 50s 360ms/step - loss: 0.0609 - accuracy: 0.9815 - val_loss: 1.3717 - val_accuracy: 0.6976
Epoch 6/30
139/139 [==============================] - 51s 366ms/step - loss: 0.0593 - accuracy: 0.9818 - val_loss: 1.2600 - val_accuracy: 0.7192
Epoch 7/30
139/139 [==============================] - 51s 363ms/step - loss: 0.0468 - accuracy: 0.9860 - val_loss: 1.1707 - val_ac